# Final Project: Finding a Perfect Locations To Open a Bar in Atlanta

## Introduction / Business Problem

For my project, I'd like to consider opening a bar in Atlanta. There are a number of factors to consider when opening up a bar, with one of the most consequential decisions being location. In this hypothetical, the bar would be aimed at young professionals who are looking for somewhere to drink when they get off work. I will be looking for locations that have a high concentration of young and middle-aged professionals with a mid-to-high degree of disposable income. 

This project would be targeted at anyone who looks to open a bar in the Atlanta area. Bars and restaurants usually operate on thin margins, so any competitive advantage in location would be beneficial to a bar owner. 

## Data

To solve this problem, we will need location data on commercial areas in atlanta. In Atlanta, as well as in other major cities, banks and law firms usually employ people that have a high degree of disposable income. In addition to these locations, colleges usually have a number of professors and other staff that make a significant amount of money. These offices are also usually in locations that have a high degree of commercial traffic. For this hypothetical, we will focus on constricting a foursquare map that reflects the locations of banks, law offices, and colleges in Atlanta. To do so, we pull data on atlanta neighborhoods from https://opendata.atlantaregional.com/datasets/d6298dee8938464294d3f49d473bcf15_196?geometry=-85.289%2C33.567%2C-83.551%2C33.967 to construct the map of Atlanta. We then use the Foursquare service to pull bank, law office, and college locations. Using k-means clustering, we find 3 ideal locations for a bar. 

The data from the Atlanta Regional Commission consists of neighborhood names, population, census data, and geographical coordinates. We will use this data to construct a choropleth map that visually represents these neighborhoods and their respective populations.

The data from Foursquare consists of location names, location types, and the geographical coordinates of the location. We will use this Foursquare data to construct Folium maps with dots representing the locations of banks, law offices, and colleges in Atlanta. 

## Methodology

#### First, we import all the necessary packages to complete the project

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0          conda-forge
    geopy:           

#### Next, we load the data from the Atlanta Regional Comission into a variable called atlanta_data

In [2]:
atlanta_data = json.loads(requests.get('https://opendata.arcgis.com/datasets/d6298dee8938464294d3f49d473bcf15_196.geojson').text)

In [3]:
atlanta_data

{'type': 'FeatureCollection',
 'name': 'City_of_Atlanta_Neighborhood_Statistical_Areas',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'OBJECTID': 1,
    'NPU': 'NPU C',
    'STATISTICA': 'C04',
    'POP2010': 2672,
    'NEIGHBORHO': 'Arden/Habersham, Argonne Forest, Peachtree Battle Alliance, Wyngate',
    'URL': 'http://documents.atlantaregional.com/AtlantaProfiles/C04.pdf',
    'A': 'Arden/Habersham, Argonne Forest, Peachtree Battle Alliance, Wyngate',
    'pop': 2672,
    'white': 96.3,
    'black': 0.9,
    'asian': 1.0,
    'other': 0.5,
    'hispanic': 1.3,
    'GlobalID': '{6018B100-48DF-4B88-85B7-C4095D15897D}',
    'last_edited_date': '1970/01/01 00:00:00+00'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-84.40728321312353, 33.8445284540347],
      [-84.40735621368728, 33.84217845397712],
      [-84.40738221308668, 33.842020453850736],
      [-84.40745021353541, 33.84185645

#### We simplify the data to only include the information under the features key

In [4]:
atl_data = atlanta_data['features']

In [5]:
atl_data[0]

{'type': 'Feature',
 'properties': {'OBJECTID': 1,
  'NPU': 'NPU C',
  'STATISTICA': 'C04',
  'POP2010': 2672,
  'NEIGHBORHO': 'Arden/Habersham, Argonne Forest, Peachtree Battle Alliance, Wyngate',
  'URL': 'http://documents.atlantaregional.com/AtlantaProfiles/C04.pdf',
  'A': 'Arden/Habersham, Argonne Forest, Peachtree Battle Alliance, Wyngate',
  'pop': 2672,
  'white': 96.3,
  'black': 0.9,
  'asian': 1.0,
  'other': 0.5,
  'hispanic': 1.3,
  'GlobalID': '{6018B100-48DF-4B88-85B7-C4095D15897D}',
  'last_edited_date': '1970/01/01 00:00:00+00'},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[-84.40728321312353, 33.8445284540347],
    [-84.40735621368728, 33.84217845397712],
    [-84.40738221308668, 33.842020453850736],
    [-84.40745021353541, 33.84185645344486],
    [-84.40749921310712, 33.84177945347297],
    [-84.4075682136065, 33.84169545317609],
    [-84.40767321307789, 33.8415994532212],
    [-84.40804721333068, 33.84131445349337],
    [-84.40816021317214, 33.8411974534646

#### We create a table with all the data that we need: Neighborhood Name, Census Data link, Population, Lattitude, and Longitude

In [6]:
column_names = ['Neighborhood','Census Data','Population', 'Latitude','Longitude']
Atlanta = pd.DataFrame(columns = column_names)

In [7]:
Atlanta

Empty DataFrame
Columns: [Neighborhood, Census Data, Population, Latitude, Longitude]
Index: []

In [8]:
for data in atl_data:
    neighborhood = data['properties']['NEIGHBORHO']
    census_data = data['properties']['URL']
    population = data['properties']['POP2010']
        
    atlanta_latlon = data['geometry']['coordinates']
    atlanta_lat = atlanta_latlon[0][0][0]
    atlanta_lon = atlanta_latlon[0][0][1]
    
    Atlanta = Atlanta.append({'Neighborhood':neighborhood,
                                          'Census Data': census_data,
                                          'Population':population,
                                          'Latitude': atlanta_lat,
                                          'Longitude': atlanta_lon
                                           },
                                            ignore_index=True)

In [9]:
Atlanta.head(10)

Neighborhood  \
0  Arden/Habersham, Argonne Forest, Peachtree Bat...   
1            Peachtree Heights East, Peachtree Hills   
2                             Peachtree Heights West   
3                 Buckhead Forest, South Tuxedo Park   
4                         Chastain Park, Tuxedo Park   
5                                 East Chastain Park   
6                                       Garden Hills   
7                                  Lindbergh/Morosgo   
8                   Buckhead Village, Peachtree Park   
9                                          Vine City   

                                         Census Data Population Latitude  \
0  http://documents.atlantaregional.com/AtlantaPr...       2672 -84.4073   
1  http://documents.atlantaregional.com/AtlantaPr...       3736 -84.3732   
2  http://documents.atlantaregional.com/AtlantaPr...       4874 -84.3846   
3  http://documents.atlantaregional.com/AtlantaPr...       3372 -84.3806   
4  http://documents.atlantaregional.com/AtlantaPr...       3423 -84.4073   
5  http://documents.atlantaregional.com/AtlantaPr...       2092 -84.3824   
6  http://documents.atlantaregional.com/AtlantaPr...       3584 -84.3832   
7  http://documents.atlantaregional.com/AtlantaPr...       4604 -84.3734   
8  http://documents.atlantaregional.com/AtlantaPr...       2920 -84.3803   
9  http://documents.atlantaregional.com/AtlantaPr...       2818 -84.4075   

  Longitude  
0   33.8445  
1    33.821  
2   33.8417  
3   33.8396  
4   33.8494  
5   33.8781  
6   33.8336  
7   33.8158  
8   33.8371  
9   33.7547

#### We create a choropleth map of the Atlanta neighborhoods using population on the color scale.  

In [10]:
address = 'Atlanta, GA'

geolocator = Nominatim(user_agent='atl_explorer')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geographical coordinate of Atlanta is {}, {}.'.format(latitude, longitude))

The geographical coordinate of Atlanta is 33.7490987, -84.3901849.


In [11]:
map_atlanta = folium.Map(location=[latitude, longitude], zoom_start=12.3, tiles='OpenStreetMap')


In [12]:
atlanta_geo = r'atlanta_data'

In [13]:
map_atlanta

threshold_scale = np.linspace(Atlanta['Population'].min(),
                             Atlanta['Population'].max(),
                             9, dtype=int)
map_atlanta.choropleth(
    geo_data=atlanta_data,
    data=Atlanta,
    columns=['Neighborhood','Population'],
    key_on='feature.properties.NEIGHBORHO',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Atlanta Population Map',
    reset=False
)

map_atlanta

In [14]:
Atlanta

Neighborhood  \
0    Arden/Habersham, Argonne Forest, Peachtree Bat...   
1              Peachtree Heights East, Peachtree Hills   
2                               Peachtree Heights West   
3                   Buckhead Forest, South Tuxedo Park   
4                           Chastain Park, Tuxedo Park   
5                                   East Chastain Park   
6                                         Garden Hills   
7                                    Lindbergh/Morosgo   
8                     Buckhead Village, Peachtree Park   
9                                            Vine City   
10                Georgia Tech, Marietta Street Artery   
11                          Castleberry Hill, Downtown   
12                                             Midtown   
13                                           Home Park   
14    Beecher Hills, Florida Heights, Westwood Terrace   
15                      Fort McPherson, Venetian Hills   
16                                        Sylvan Hills   
17                    Capitol View, Capitol View Manor   
18                         Bush Mountain, Oakland City   
19                                            Westview   
20                                            West End   
21             Ashview Heights, Harris Chiles, Just Us   
22   Atlanta University Center, The Villages at Cas...   
23                 Center Hill, Harvel Homes Community   
24          Dixie Hills, Penelope Neighbors, West Lake   
25   Brandon, Castlewood, Westminster/Milmar, Woodf...   
26   Kingswood, Mt. Paran/Northside, Mt. Paran Park...   
27                                        Hammond Park   
28   Blair Villa/Poole Creek, Glenrose Heights, Orc...   
29                                 South River Gardens   
30                                           Perkerson   
31   Amal Heights, Betmar LaVilla, High Point, Joyland   
32                                      English Avenue   
33                Berkeley Park, Blandtown, Hills Park   
34                                     Underwood Hills   
35   Channing Valley, Memorial Park, Springlake, Wi...   
36             Margaret Mitchell, Paces, Pleasant Hill   
37   Fernleaf, Hanover West, Ridgewood Heights, Wes...   
38                                         Cross Creek   
39   Browns Mill Park, Polar Rock, Swallow Circle/B...   
40               South Atlanta, The Villages at Carver   
41                                    Lakewood Heights   
42                              Adair Park, Pittsburgh   
43                                      Mechanicsville   
44                                         Peoplestown   
45                         Capitol Gateway, Summerhill   
46   Lakewood, Leila Valley, Norwood Manor, Rebel V...   
47                                          Grove Park   
48                             Almond Park, Carey Park   
49            Bolton, Riverside, Whittier Mill Village   
50   Carver Hills, Rockdale, Scotts Crossing, West ...   
51                           Hunter Hills, Mozley Park   
52                           Bankhead, Washington Park   
53                          Knight Park/Howell Station   
54                      Midwest Cascade, Regency Trace   
55   Arlington Estates, Ben Hill, Butner/Tell, Elmc...   
56                                     Princeton Lakes   
57   Ben Hill Forest, Ben Hill Pines, Brentwood, De...   
58                                          Greenbriar   
59                                             Airport   
60   Ashley Courts, Greenbriar Village, Niskey Cove...   
61   Ben Hill Terrace, Kings Forest, Old Fairburn V...   
62   Bankhead Courts, Bankhead/Bolton, Carroll Heig...   
63                                     Collier Heights   
64   Atlanta Industrial Park, Bolton Hills, Brookvi...   
65          Campbellton Road, Fort Valley, Pomona Park   
66   Audobon Forest, Audobon Forest West, Chalet Wo...   
67                                 Cascade Avenue/Road   
68   Baker Hills, Bakers Ferry, Boulder 

In [15]:
CLIENT_ID = 'T0LRXY51HVVKPRWVPAANAE0PGUPBDOMJT3VMFLTXA0EFT1B2' # your Foursquare ID
CLIENT_SECRET = '212YUF3ILKXGFIYENNUHGRRIUXIPQI02FVB54QCVIUT11ADL' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: T0LRXY51HVVKPRWVPAANAE0PGUPBDOMJT3VMFLTXA0EFT1B2
CLIENT_SECRET:212YUF3ILKXGFIYENNUHGRRIUXIPQI02FVB54QCVIUT11ADL


In [16]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

#### We then create a map with circle markers to represent the locations of different types of locations. First we create a map with markers to represent the location of banks. 

In [17]:
LIMIT = 300 # limit of number of venues returned by Foursquare API

radius = 7000 # define radius

search_query = 'Bank'



# create URL
url1 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET,  
    33.7490, 
    -84.3880,
    VERSION,
    search_query,
    radius, 
    LIMIT)
url1

'https://api.foursquare.com/v2/venues/explore?client_id=T0LRXY51HVVKPRWVPAANAE0PGUPBDOMJT3VMFLTXA0EFT1B2&client_secret=212YUF3ILKXGFIYENNUHGRRIUXIPQI02FVB54QCVIUT11ADL&ll=33.749,-84.388&v=20180605&query=Bank&radius=7000&limit=300'

In [18]:
results1 = requests.get(url1).json()
results1

{'meta': {'code': 200, 'requestId': '5efbe6cbd76da7739972deb6'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Atlanta',
  'headerFullLocation': 'Atlanta',
  'headerLocationGranularity': 'city',
  'query': 'bank',
  'totalResults': 145,
  'suggestedBounds': {'ne': {'lat': 33.81200006300006,
    'lng': -84.31237282080842},
   'sw': {'lat': 33.68599993699994, 'lng': -84.46362717919159}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b1d11d3f964a520950b24e3',
       'name': 'SunTrust Plaza',
       'location': {'address': '303 Peachtree St NE',
        'lat': 33.76238950622084,
        'lng': -84.38596229670338,
        'labeledLatLngs': [{'label': 'display',
          'lat': 33.

In [19]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [20]:
venues = results1['response']['groups'][0]['items']
    
bank_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
bank_venues =bank_venues.loc[:, filtered_columns]

# filter the category for each row
bank_venues['venue.categories'] = bank_venues.apply(get_category_type, axis=1)

# clean columns
bank_venues.columns = [col.split(".")[-1] for col in bank_venues.columns]

bank_venues = bank_venues[~bank_venues.name.str.contains('ATM')]

bank_venues



name    categories        lat  \
0                                   SunTrust Plaza          Bank  33.762390   
1                                  Bank of America          Bank  33.760172   
2                                         Suntrust          Bank  33.754646   
4                                             BB&T          Bank  33.760032   
5                                      Wells Fargo          Bank  33.757481   
6                                      Wells Fargo          Bank  33.738222   
7                                         SunTrust          Bank  33.760945   
8                                  Bank of America          Bank  33.770895   
9                                    SunTrust Bank          Bank  33.755113   
10                                     Wells Fargo          Bank  33.758551   
11                                   SunTrust Bank          Bank  33.769071   
12                 Federal Reserve Bank of Atlanta          Bank  33.782233   
13                                            ATDC          Bank  33.777233   
14                                        SunTrust          Bank  33.774036   
15                                     Wells Fargo          Bank  33.754226   
16                               Thomas Moore Bank          Bank  33.748711   
17                    271 Building (BB&T Building)          Bank  33.791592   
18                                   SunTrust Bank          Bank  33.754907   
19       Georgia’s Own Credit Union - AT&T Midtown  Credit Union  33.773124   
20                                 NMPL Atlanta-GA          Bank  33.750535   
21                                     Wells Fargo          Bank  33.772548   
22                              MintLink Solutions          Bank  33.746806   
23                               Capitol City Bank          Bank  33.752411   
24                                 Bank of America          Bank  33.755145   
25                                     Wells Fargo          Bank  33.760817   
26                                     Wells Fargo          Bank  33.782077   
27                                iTHINK Financial          Bank  33.753502   
28                                   Fidelity Bank          Bank  33.748363   
29                                 Bank of America          Bank  33.784308   
30                         BB&T - Peachtree Center          Bank  33.760147   
31                          Buffie The Tax Heiress          Bank  33.749667   
32                              Human Services ECU          Bank  33.756650   
33  Fifth Third Business Banking - Russell Jackson          Bank  33.757446   
34                                    PNC Building          Bank  33.777238   
35                                        SunTrust          Bank  33.795598   
36                             Citizens Trust Bank          Bank  33.759207   
37                                     Wells Fargo          Bank  33.738783   
38                                      Chase Bank          Bank  33.721445   
39                                      Chase Bank          Bank  33.757123   
40                                      Chase Bank          Bank  33.759834   
41                                            SECU          Bank  33.745022   
42                                Wells Fargo Bank          Bank  33.774131   
43                                  Sun Trust Bank          Bank  33.761001   
44                                    Regions Bank          Bank  33.786972   
45                                    Regions Bank          Bank  33.786979   
46                             SunTrust University          Bank  33.761196   
47                                        PNC Bank          Bank  33.783566   
48                                     Ameris Bank          Bank  33.761450   
49                                            BB&T          Bank  33.778122   
50                             C & C Check Cashing          Bank  33.754885   
51               

In [21]:
for lat, lng, name in zip(bank_venues['lat'], bank_venues['lng'], bank_venues['name']):
    label = '{}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='black',
        fill_opacity=1,
        parse_html=False).add_to(map_atlanta)


In [22]:
map_atlanta

#### We then create circle markers to represent the location of law offices. 

In [23]:
LIMIT = 300 # limit of number of venues returned by Foursquare API

radius = 7000 # define radius

search_query = 'Law'



# create URL
url2 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET,  
    33.7490, 
    -84.3880,
    VERSION,
    search_query,
    radius, 
    LIMIT)
url2

results2 = requests.get(url2).json()
results2

venues = results2['response']['groups'][0]['items']
    
law_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
law_venues =law_venues.loc[:, filtered_columns]

# filter the category for each row
law_venues['venue.categories'] = law_venues.apply(get_category_type, axis=1)

# clean columns
law_venues.columns = [col.split(".")[-1] for col in law_venues.columns]

law_venues

name  \
0                              The Ford Law Firm P.C.   
1                Georgia State University Law Library   
2                  Atlanta's John Marshall Law School   
3   Atlanta's John Marshall Law School's PB Adcock...   
4   Atlanta's John Marshall Law School: T. C. Sino...   
5                  The Law Office of Donald P Edwards   
6                        Scheller College Of Business   
7                                   Hornsby Law Group   
8                    N. Sandy Epstein Attorney At Law   
9                              Urban Life Law Library   
10                       Edmond, Lindsay & Atkins LLP   
11                         Bader Scott Injury Lawyers   
12                             Melville Johnson, P.C.   
13                                  Ballard Spahr LLP   
14                                 The Herro Law Firm   
15                        Atlanta Southwest Probation   
16  The Atlanta Law Offices of Williams and Willia...   
17                Jeffrey Flynn, P.C. Attorney At Law   
18                               Parsons & Associates   
19      The Law Offices of Nathaniel F. Hansford, LLC   
20                               State Bar Of Georgia   
21                    Bondurant, Mixson & Elmore, LLP   
22                         Municipal Court of Atlanta   
23              Georgia Department of Driver Services   

                   categories        lat        lng  
0                  Law School  33.755520 -84.390312  
1                  Law School  33.756638 -84.385813  
2                  Law School  33.793224 -84.388241  
3                  Law School  33.793624 -84.388201  
4                  Law School  33.793284 -84.388564  
5                      Lawyer  33.750887 -84.393410  
6   College Academic Building  33.776262 -84.387893  
7                      Lawyer  33.786972 -84.388245  
8                      Lawyer  33.759534 -84.388448  
9             College Library  33.751327 -84.385887  
10                     Lawyer  33.745693 -84.376338  
11                     Lawyer  33.761430 -84.388349  
12                     Lawyer  33.778931 -84.386559  
13                     Office  33.780759 -84.383745  
14                     Lawyer  33.787114 -84.387263  
15                     Office  33.725054 -84.417756  
16                     Lawyer  33.791544 -84.394664  
17                     Lawyer  33.794333 -84.386691  
18         Miscellaneous Shop  33.786499 -84.397054  
19                     Lawyer  33.794333 -84.386691  
20        Government Building  33.756422 -84.392485  
21            Coworking Space  33.787208 -84.387803  
22                 Courthouse  33.747531 -84.393280  
23        Government Building  33.742777 -84.388793

In [24]:
for lat, lng, name in zip(law_venues['lat'], law_venues['lng'], law_venues['name']):
    label = '{}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='purple',
        fill=True,
        fill_color='black',
        fill_opacity=1,
        parse_html=False).add_to(map_atlanta)

map_atlanta

#### We then create a circle marker to represent the location of college buildings

In [25]:
LIMIT = 300 # limit of number of venues returned by Foursquare API

radius = 7000 # define radius

search_query = 'College'



# create URL
url2 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET,  
    33.7490, 
    -84.3880,
    VERSION,
    search_query,
    radius, 
    LIMIT)
url2

results2 = requests.get(url2).json()
results2

venues = results2['response']['groups'][0]['items']
    
college_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
college_venues =college_venues.loc[:, filtered_columns]

# filter the category for each row
college_venues['venue.categories'] = college_venues.apply(get_category_type, axis=1)

# clean columns
college_venues.columns = [col.split(".")[-1] for col in college_venues.columns]

college_venues

for lat, lng, name in zip(college_venues['lat'], college_venues['lng'], college_venues['name']):
    label = '{}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='black',
        fill_opacity=0.2,
        parse_html=False).add_to(map_atlanta)

map_atlanta

In [26]:
map_atlanta

#### We then put all of the tables together into one table

In [27]:
office_venues = pd.concat([bank_venues, law_venues, college_venues])

In [28]:
office_venues

name  \
0                                      SunTrust Plaza   
1                                     Bank of America   
2                                            Suntrust   
4                                                BB&T   
5                                         Wells Fargo   
6                                         Wells Fargo   
7                                            SunTrust   
8                                     Bank of America   
9                                       SunTrust Bank   
10                                        Wells Fargo   
11                                      SunTrust Bank   
12                    Federal Reserve Bank of Atlanta   
13                                               ATDC   
14                                           SunTrust   
15                                        Wells Fargo   
16                                  Thomas Moore Bank   
17                       271 Building (BB&T Building)   
18                                      SunTrust Bank   
19          Georgia’s Own Credit Union - AT&T Midtown   
20                                    NMPL Atlanta-GA   
21                                        Wells Fargo   
22                                 MintLink Solutions   
23                                  Capitol City Bank   
24                                    Bank of America   
25                                        Wells Fargo   
26                                        Wells Fargo   
27                                   iTHINK Financial   
28                                      Fidelity Bank   
29                                    Bank of America   
30                            BB&T - Peachtree Center   
31                             Buffie The Tax Heiress   
32                                 Human Services ECU   
33     Fifth Third Business Banking - Russell Jackson   
34                                       PNC Building   
35                                           SunTrust   
36                                Citizens Trust Bank   
37                                        Wells Fargo   
38                                         Chase Bank   
39                                         Chase Bank   
40                                         Chase Bank   
41                                               SECU   
42                                   Wells Fargo Bank   
43                                     Sun Trust Bank   
44                                       Regions Bank   
45                                       Regions Bank   
46                                SunTrust University   
47                                           PNC Bank   
48                                        Ameris Bank   
49                                               BB&T   
50                                C & C Check Cashing   
51                                        Wells Fargo   
53                                  ATT Southern Inc.   
54                         State Bank & Trust Company   
55                                           PNC Bank   
56                                           SunTrust   
57                                          Money Pit   
58                         Bank of America - Downtown   
59                                       Regions Bank   
60                                   Fifth third bank   
61                                    Bank of America   
62                         Georgia's Own Credit Union   
63                                               APCU   
64                                               APCU   
65                                    Bank of America   
66                                SunTrust Centennial   
67                                    Bank of America   
68                             Bank Of America Branch   
69                            Pf Chang Pop Up In Bofa   
70                                  Capitol City Bank   
71                                  Jack & Ace Cigars   
72

#### Using the lattitude and longitude of the office venues table, we will construct a k means test to determine the ideal locations. 

In [29]:
kclusters = 4

areas_grouped_clustering = office_venues.drop('name', 1)
areas_grouped_clustering = areas_grouped_clustering.drop('categories',1)

kmeans = KMeans(n_clusters = kclusters, random_state = 0).fit(areas_grouped_clustering)

kmeans.labels_[:]

array([0, 0, 0, 0, 0, 2, 0, 1, 0, 3, 1, 1, 1, 1, 0, 0, 1, 2, 1, 0, 1, 0,
       0, 0, 0, 3, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 2, 3, 3, 0, 2, 3, 0, 1,
       1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 2, 0, 1, 2, 3, 0, 0, 0, 1, 1, 1,
       1, 1, 2, 2, 1, 1, 2, 1, 2, 3, 1, 2, 1, 3, 3, 3, 3, 1, 3, 3, 3, 1,
       1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 1, 2, 1,
       1, 1, 1, 0, 1, 0, 0, 2, 3, 2, 2, 0, 2, 0, 1, 0, 0, 0, 0, 0, 1, 0,
       1, 0, 0, 0, 2, 2, 0, 1, 0, 0, 0, 0, 0, 2, 0, 2, 0, 0, 1, 1, 1, 2,
       2, 1, 2, 2, 1, 1, 2, 1, 1, 3, 1, 1, 1, 1, 2, 0, 1, 0, 1, 0, 1, 0,
       1, 1, 0, 0, 2, 0, 1, 1, 1, 1, 1, 1, 1, 2, 0, 1, 0, 0, 2, 2, 0, 2,
       2, 1, 1, 0, 2, 2, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1],
      dtype=int32)

In [30]:
centerval = kmeans.cluster_centers_.tolist()

In [31]:
centerval

[[33.75426017963511, -84.38841764709295],
 [33.781516483100475, -84.39118209533241],
 [33.738193887011334, -84.41064940397149],
 [33.75778079158816, -84.35372534089916]]

In [32]:
potentialloc = pd.DataFrame(centerval)

In [33]:
potentialloc

0          1
0  33.754260 -84.388418
1  33.781516 -84.391182
2  33.738194 -84.410649
3  33.757781 -84.353725

In [34]:
potentialloc.columns = ['lat','lng']

In [35]:
potentialloc

lat        lng
0  33.754260 -84.388418
1  33.781516 -84.391182
2  33.738194 -84.410649
3  33.757781 -84.353725

In [36]:
for lat, lng in zip(potentialloc['lat'], potentialloc['lng']):
    label = 'Potential Location'
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=1,
        parse_html=False).add_to(map_atlanta)


In [37]:
map_atlanta

## Results

Using k-means clustering, we find four potential locations for a bar. One location is in Downtown Atlanta, another in Midtown Atlanta, another in Inman Park, and one in Pittsburg. Based on the population data from the choropleth map, the Downtown and Midtown locations would be the most ideal.

## Conclusion

Based on the population data from the choropleth map, the Downtown and Midtown locations would be the most ideal. They have the highest populations of the four locations, and a cursory glance at the location of the cluster centers shows that these locations are located near a number of banks, law offices and college buildings.

In the future, there are two recommendations that I would make. First, there should be an analysis of the number of bars in the areas. If there are too many bars in a limited radius, they could cannibalize the market for a new bar. Second, there should be an analysis of the age of a bar. Old